In [4]:
##################################################################################################################
##################################################################################################################
###############################################ngrams representation###############################################
##################################################################################################################
##################################################################################################################

In [5]:
import warnings
warnings.filterwarnings('ignore')

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 

import gensim
import gensim.corpora as corpora
from gensim.models.coherencemodel import CoherenceModel
from sklearn.feature_extraction.text import TfidfVectorizer

import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
nltk.download('stopwords')
from nltk.stem.wordnet import WordNetLemmatizer
nltk.download('wordnet')

from pprint import pprint

from textblob import TextBlob, Word

import spacy
#loading the english language small model of spacy
en = spacy.load('en_core_web_sm')
sw_spacy = en.Defaults.stop_words

import pickle
import re 
import pyLDAvis
import pyLDAvis.gensim_models

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Wahbeh\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Wahbeh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [6]:
df = pd.read_csv ('sample.csv')

In [7]:
#Remove non english tweets
nlp = spacy.load("en_core_web_sm")
STOPWORDS_DICT = {lang: set(nltk.corpus.stopwords.words(lang)) for lang in nltk.corpus.stopwords.fileids()}

def get_language(text):
    #Determines what language the comment is written in and filters only English comments.
    words = set(nltk.wordpunct_tokenize(text.lower()))
    return max(((lang, len(words & stopwords)) for lang, stopwords in STOPWORDS_DICT.items()), key = lambda x: x[1])[0]

df['language'] = df['Full Text'].map(get_language)
df = df.loc[df['language'] == 'english']
df = df.drop('language', axis=1)
df = df[df['Full Text'] != ""]

In [8]:
df

Full Text
0     @hamcore_ First the boss metal zone schematics...
1     @sippygup its in the vaccine and 5g makes it m...
2     Him and all the others that do Not like and ha...
3     @TimRunsHisMouth Him and all the others that d...
4     @NYGovCuomo 99.97% survival rate no vaccine fo...
...                                                 ...
9953  Waiting for the train and I hear two mfs say �...
9954  I played my radical left avant garde music and...
9955  You are such a fag @MayorKeller And what the F...
9956  .@seanspicer hahahaha Trump's accomplishments?...
9957  100%. It was about the election, not the virus...

[9778 rows x 1 columns]

In [9]:
df= df.apply(lambda x: x.astype(str).str.lower())

In [10]:
df.head()

Full Text
0  @hamcore_ first the boss metal zone schematics...
1  @sippygup its in the vaccine and 5g makes it m...
2  him and all the others that do not like and ha...
3  @timrunshismouth him and all the others that d...
4  @nygovcuomo 99.97% survival rate no vaccine fo...

# Pre-processing

In [11]:
docs = np.array(df['Full Text'])

In [12]:
def clean_tweets(docs):
    for i in range(len(docs)):
        #remove hashtags and mentions
        docs[i] = " ".join(filter(lambda x:x[0]!='#', docs[i].split())) #remove hashtags
        docs[i] = " ".join(filter(lambda x:x[0]!='@', docs[i].split())) #remove mentiones
        
        #remove special chars, anything not a number or letter, anything excpet alphanumeric words
        docs[i] = re.sub(r'[^\w\s]','',docs[i]) #remove punctuation marks and special chars
        docs[i] = re.sub('[^A-Za-z0-9]+', ' ', docs[i]) #remove anything that is not a number or or letter
        docs[i] = re.sub('[\W_]', ' ', docs[i]) #Remove any thing excpet charcater and alphanumeric words
        docs[i] = ' '.join(word for word in docs[i].split() if not word.isdigit())
        
        #Remove stop words using spacy
        words = [word for word in docs[i].split() if word.lower() not in sw_spacy]
        docs[i] = " ".join(words)
        
        #remove words that consists of single letter
        words = [word for word in docs[i].split() if len(word)>1]
        docs[i] = " ".join(words)
                             
        #Lemmatize each tweet
        sent = TextBlob(docs[i])
        docs[i] = " ". join([w.lemmatize() for w in sent.words])
    return docs

<>:10: DeprecationWarning: invalid escape sequence \W
<>:10: DeprecationWarning: invalid escape sequence \W
C:\Users\Wahbeh\AppData\Local\Temp/ipykernel_28632/927281990.py:10: DeprecationWarning: invalid escape sequence \W
  docs[i] = re.sub('[\W_]', ' ', docs[i]) #Remove any thing excpet charcater and alphanumeric words


In [13]:
processed_docs = clean_tweets(docs)

In [14]:
processed_docs

array(['bos metal zone schematic 5g vaccine hitler got stuff right cmon man 1042am',
       'vaccine 5g make powerful watch',
       'like hate donaldtrump satanic deep state illuminati serf differentgod god gave power poisoning food water thats monsanto plus vaccine withvp',
       ...,
       'fag fuck que que logo stupid waste time money mask distancing testing vaccine',
       'seanspicer hahahaha trump accomplishment vaccine international company working trump acknowledged pandemic economy rallied biden won transition started trump killed farmer',
       'election virus vaccine control virus biggest psychological operation perpetrated american people people world'],
      dtype=object)

# Generate bigram and trigram

In [15]:
from nltk import ngrams
ngram_list = []
for i in range(len(processed_docs)):
    doc = processed_docs[i]
    bigram = ngrams(doc.split(' '), n=2)
    trigram = ngrams(doc.split(' '), n=3)
    ngram_docs = []
    for x in bigram:
        ngram_docs.append(' '.join(x))
    for y in trigram:
        ngram_docs.append(' '.join(y))
    ngram_list.append(ngram_docs)

In [16]:
ngram_list[1]

['vaccine 5g',
 '5g make',
 'make powerful',
 'powerful watch',
 'vaccine 5g make',
 '5g make powerful',
 'make powerful watch']

In [17]:
docs = ngram_list

In [18]:
from gensim.corpora import Dictionary

# Create a dictionary representation of the documents.
docs_dict = Dictionary(docs)
print('Number of unique words in initital documents:', len(docs_dict))

# #Filter out words that occur less than 10 documents, or more than 40% of the documents.
# docs_dict.filter_extremes(no_below=2, no_above=0.60)
# print('Number of unique words after removing rare and common words:', len(docs_dict))

Number of unique words in initital documents: 171254


In [19]:
for key, i in docs_dict.items():
    print(key, i)

0 5g vaccine
1 5g vaccine hitler
2 bos metal
3 bos metal zone
4 cmon man
5 cmon man 1042am
6 got stuff
7 got stuff right
8 hitler got
9 hitler got stuff
10 man 1042am
11 metal zone
12 metal zone schematic
13 right cmon
14 right cmon man
15 schematic 5g
16 schematic 5g vaccine
17 stuff right
18 stuff right cmon
19 vaccine hitler
20 vaccine hitler got
21 zone schematic
22 zone schematic 5g
23 5g make
24 5g make powerful
25 make powerful
26 make powerful watch
27 powerful watch
28 vaccine 5g
29 vaccine 5g make
30 deep state
31 deep state illuminati
32 differentgod god
33 differentgod god gave
34 donaldtrump satanic
35 donaldtrump satanic deep
36 food water
37 food water thats
38 gave power
39 gave power poisoning
40 god gave
41 god gave power
42 hate donaldtrump
43 hate donaldtrump satanic
44 illuminati serf
45 illuminati serf differentgod
46 like hate
47 like hate donaldtrump
48 monsanto plus
49 monsanto plus vaccine
50 plus vaccine
51 plus vaccine withvp
52 poisoning food
53 poisoning f

683 micro micro dust
684 nazi guvs
685 nazi guvs exposed
686 pelosi goon
687 pelosi goon bg
688 vaccine nazi
689 vaccine nazi guvs
690 year mapped
691 year mapped dusty
692 5g connect
693 5g connect brain
694 artificial intelligence
695 artificial intelligence 5g
696 away vaccine
697 away vaccine loaded
698 brain internet
699 brain internet cyborg
700 connect brain
701 connect brain internet
702 cyborg eradicating
703 cyborg eradicating human
704 darpa profusa
705 darpa profusa hydrogel
706 eradicating human
707 eradicating human race
708 fuck away
709 fuck away vaccine
710 human race
711 human race ushering
712 hydrogel artificial
713 hydrogel artificial intelligence
714 intelligence 5g
715 intelligence 5g connect
716 internet cyborg
717 internet cyborg eradicating
718 loaded darpa
719 loaded darpa profusa
720 new race
721 new race transhumans
722 profusa hydrogel
723 profusa hydrogel artificial
724 race transhumans
725 race ushering
726 race ushering new
727 stay fuck
728 stay fuck a

1640 didnt patriot stand
1641 force vaccination
1642 force vaccination deep
1643 hillary barack
1644 hillary barack denounce
1645 nation covid19
1646 nation covid19 camp
1647 patriot stand
1648 patriot stand want
1649 stand want
1650 stand want hillary
1651 state united
1652 state united nation
1653 trump denounce
1654 trump denounce didnt
1655 united nation
1656 united nation covid19
1657 vaccination deep
1658 vaccination deep state
1659 want hillary
1660 want hillary barack
1661 5g invent
1662 5g invent covid
1663 actor makeup
1664 actor makeup sandy
1665 breed plant
1666 breed plant penny
1667 covid microchip
1668 covid microchip vaccine
1669 dems election
1670 dems election validate
1671 election validate
1672 election validate ga
1673 exact moment
1674 exact moment tell
1675 ga vote
1676 ga vote breed
1677 hire actor
1678 hire actor makeup
1679 hook implement
1680 hook implement 5g
1681 implement 5g
1682 implement 5g invent
1683 invent covid
1684 invent covid microchip
1685 makeup

2653 lord libs
2654 lord libs charge
2655 oh lord
2656 oh lord libs
2657 outbreak warned
2658 reminds venezuelan
2659 reminds venezuelan gaytanic
2660 satanic socialist
2661 satanic socialist reminds
2662 socialist reminds
2663 socialist reminds venezuelan
2664 turn gay
2665 turn gay satanic
2666 vaccination turn
2667 vaccination turn gay
2668 venezuelan gaytanic
2669 venezuelan gaytanic baby
2670 asahutchinson forceinjecting
2671 asahutchinson forceinjecting citizen
2672 bill forceinjecting
2673 bill forceinjecting citizen
2674 bsample bill
2675 bsample bill forceinjecting
2676 bunker like
2677 bunker like hussein
2678 continue spread
2679 continue spread test
2680 distance vaccine
2681 distance vaccine trial
2682 donaldtrump found
2683 donaldtrump found guilty
2684 dragout bunker
2685 dragout bunker like
2686 fired dragout
2687 fired dragout bunker
2688 found guilty
2689 found guilty fired
2690 guilty fired
2691 guilty fired dragout
2692 hussein husain
2693 like hussein
2694 like hus

3517 happen got covid
3518 happen neighbor
3519 happen neighbor voted
3520 health threat
3521 health threat sent
3522 howd happen
3523 howd happen neighbor
3524 internment camp
3525 internment camp howd
3526 law ok
3527 law ok disease
3528 medical privacy
3529 medical privacy law
3530 neighbor voted
3531 ok disease
3532 ok disease happen
3533 positive refuse
3534 positive refuse vaccine
3535 privacy law
3536 privacy law ok
3537 public health threat
3538 refuse vaccine
3539 refuse vaccine youre
3540 sent internment
3541 sent internment camp
3542 test positive
3543 test positive refuse
3544 threat sent
3545 threat sent internment
3546 vaccine youre
3547 vaccine youre declared
3548 violation federal
3549 violation federal medical
3550 youre declared
3551 youre declared public
3552 5g tower coordinate
3553 add clinton
3554 add clinton grand
3555 bill gate chip
3556 china george
3557 china george soros
3558 chip vaccine total
3559 clinton grand
3560 clinton grand unified
3561 conspiracy the

...

167439 ppl starting covid
167440 president clearly
167441 president clearly work
167442 start thank
167443 start thank mrpresident
167444 starting covid
167445 starting covid vaccine
167446 state cant america
167447 thank mrpresident
167448 work good american
167449 big family
167450 big family dinner
167451 cooked big
167452 cooked big family
167453 dinner yes
167454 dinner yes know
167455 family dinner
167456 family dinner yes
167457 fear cold
167458 felt good
167459 felt good cooked
167460 fine stop
167461 fine stop hoax
167462 good cooked
167463 good cooked big
167464 hoax vaccine necessary
167465 know people sicker
167466 liberty fear cold
167467 mom felt
167468 mom felt good
167469 necessary liberty
167470 necessary liberty fear
167471 people sicker
167472 people sicker fine
167473 sicker fine
167474 sicker fine stop
167475 stop hoax
167476 stop hoax vaccine
167477 vaccine necessary liberty
167478 ability shape
167479 ability shape shift
167480 ballot illuminati
167481 ballot ill

168422 dr info chemical
168423 info chemical
168424 info chemical proposed
168425 let targeted
168426 let targeted dna
168427 like strep
168428 like strep magnetic
168429 magnetic 5g
168430 proposed vaccine
168431 proposed vaccine let
168432 rna like
168433 rna like strep
168434 strep magnetic
168435 strep magnetic 5g
168436 targeted dna
168437 targeted dna rna
168438 vaccine let targeted
168439 5g tracking tag
168440 able travel freely
168441 accepting vaccine 5g
168442 beast die
168443 beast die democrat
168444 democrat people
168445 die democrat
168446 die democrat people
168447 freely accepting
168448 freely accepting vaccine
168449 longer able
168450 longer able buy
168451 longer able travel
168452 mark beast die
168453 mask longer
168454 mask longer able
168455 sell trade wearing
168456 tag mark
168457 tag mark beast
168458 tracking tag
168459 tracking tag mark
168460 trade wearing
168461 trade wearing mask
168462 travel freely
168463 travel freely accepting
168464 wearing mask l

169315 produced pharma company
169316 question censored
169317 question censored corporate
169318 speed animal
169319 speed animal study
169320 study human
169321 study human guinea
169322 vaccine produced pharma
169323 warp speed animal
169324 wonder warp
169325 wonder warp speed
169326 proponent idea
169327 proponent idea vaccine
169328 brighter new
169329 brighter new world
169330 dont shine fraudchi
169331 future brighter
169332 future brighter new
169333 great reset shove
169334 illness future
169335 illness future brighter
169336 kill great
169337 kill great reset
169338 life illness
169339 life illness future
169340 order vaccine kill
169341 reset shove
169342 reset shove sun
169343 sacrifice save
169344 sacrifice save life
169345 save life illness
169346 shine fraudchi
169347 shove sun dont
169348 vaccine kill great
169349 5gu ur
169350 5gu ur homework
169351 baby part surveillance
169352 chain vaccine
169353 chain vaccine change
169354 change ur
169355 change ur dna
169356 dem

170262 digital currency debt
170263 dollar forced
170264 dollar forced use
170265 election theft
170266 election theft march
170267 eventual vaccine
170268 eventual vaccine mandate
170269 fear mongering mask
170270 fire right
170271 fire right lockdown
170272 forced use
170273 forced use digital
170274 great reset nwo
170275 iron fire
170276 iron fire right
170277 mandate stop use
170278 manipulation election
170279 manipulation election theft
170280 march great
170281 march great reset
170282 mask eventual
170283 mask eventual vaccine
170284 mongering mask
170285 mongering mask eventual
170286 nwo deep
170287 nwo deep state
170288 reset nwo
170289 reset nwo deep
170290 right lockdown
170291 right lockdown fear
170292 stop use
170293 stop use dollar
170294 theft march
170295 theft march great
170296 use digital
170297 use digital currency
170298 use dollar
170299 use dollar forced
170300 allow happen
170301 allow happen allow
170302 allow hyped
170303 allow hyped pandemic
170304 danger

171179 satanic signal
171180 satanic signal send
171181 send 5g
171182 send 5g tower
171183 signal send
171184 signal send 5g
171185 system way
171186 system way vaccination
171187 tower control voting
171188 voting system
171189 voting system way
171190 way vaccination
171191 fag fuck
171192 fag fuck que
171193 fuck que
171194 fuck que que
171195 logo stupid
171196 logo stupid waste
171197 money mask distancing
171198 que logo
171199 que logo stupid
171200 que que
171201 que que logo
171202 stupid waste
171203 stupid waste time
171204 time money mask
171205 accomplishment vaccine international
171206 acknowledged pandemic
171207 acknowledged pandemic economy
171208 biden won transition
171209 company working
171210 company working trump
171211 economy rallied
171212 economy rallied biden
171213 hahahaha trump
171214 hahahaha trump accomplishment
171215 international company
171216 international company working
171217 killed farmer
171218 pandemic economy
171219 pandemic economy rallie

In [20]:
#bag of words representation
corpus = [docs_dict.doc2bow(doc) for doc in docs]
corpus[0]

[(0, 1),
 (1, 1),
 (2, 1),
 (3, 1),
 (4, 1),
 (5, 1),
 (6, 1),
 (7, 1),
 (8, 1),
 (9, 1),
 (10, 1),
 (11, 1),
 (12, 1),
 (13, 1),
 (14, 1),
 (15, 1),
 (16, 1),
 (17, 1),
 (18, 1),
 (19, 1),
 (20, 1),
 (21, 1),
 (22, 1)]

In [21]:
corpus[55]

[(0, 1),
 (1279, 1),
 (1280, 1),
 (1281, 1),
 (1282, 1),
 (1283, 1),
 (1284, 1),
 (1285, 1),
 (1286, 1)]

In [22]:
print('Number of unique tokens: %d' % len(docs_dict))
print('Number of documents: %d' % len(corpus))

Number of unique tokens: 171254
Number of documents: 9778


# LDA topic model

In [23]:
from gensim.models import LdaModel
from gensim.models.coherencemodel import CoherenceModel

In [38]:
import logging

# Set up log to external log file
# Remove all handlers associated with the root logger object.
for handler in logging.root.handlers[:]:
    logging.root.removeHandler(handler)
    
logging.basicConfig(filename='lda_model.log', format='%(asctime)s : %(levelname)s : %(message)s', 
                    level=logging.INFO)

In [39]:
# Set training parameters.
num_topics = 51
chunksize = 10000 # size of the doc looked at every pass
passes = 40 # number of passes through documents
iterations = 100
eval_every = 1  # Don't evaluate model perplexity, takes too much time.

# Make an index to word dictionary.
temp = docs_dict[0]  # This is only to "load" the dictionary.
id2word = docs_dict.id2token

%time model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes, eval_every=eval_every)

Wall time: 4min 30s


In [40]:
# Compute model Perplexity - a measure of how good the model is. lower the better`
print('\nPerplexity: ', model.log_perplexity(corpus,total_docs=9958))  

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=model, texts=docs, dictionary=docs_dict , coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -12.741900791126398

Coherence Score:  0.54283384067356


# Creating a base model

In [41]:
%time model = LdaModel(corpus=corpus, id2word=id2word, num_topics = 50, random_state=100, \
                       chunksize=10000, passes=10)

Wall time: 1min 6s


In [42]:
 #How good a given topic model is?
    
# Compute model Perplexity - a measure of how good the model is. lower the better`
print('\nPerplexity: ', model.log_perplexity(corpus,total_docs=9778))  

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=model, texts=docs, dictionary=docs_dict , coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -12.739635134306742

Coherence Score:  0.5380045197704572


# Improve Coherence: Optimizing LDA Model

In [24]:
def compute_coherence_values(id2word, dictionary, corpus, texts, limit, start=2, step=1):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    
    # Fixed LDA model parameters
    chunksize = 10000 # size of the doc looked at every pass
    passes = 40 # number of passes through documents
    iterations = 100
    #eval_every = 10  # Don't evaluate model perplexity, takes too much time.

    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        print("LDA model with ", num_topics, "topics")
        model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes)
        model_list.append(model)
        
        print("Calculating coherence score")
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values

In [25]:
model_list, coherence_values = compute_coherence_values(id2word=id2word, dictionary=docs_dict, \
                                                        corpus=corpus, texts=docs, start=2, limit=51, step=1)

NameError: name 'id2word' is not defined

In [ ]:
# Show graph
limit=51; start=2; step=1;
x = range(start, limit, step)
plt.plot(x, coherence_values)
plt.xlabel("Num Topics")
plt.ylabel("Coherence score")
plt.legend(("coherence_values"), loc='best')
plt.show()# Print the coherence scores

In [46]:
# Print the coherence scores
for m, cv in zip(x, coherence_values):
    print("Num Topics =", m, " has Coherence Value of", round(cv, 4))

Num Topics = 2  has Coherence Value of 0.4901
Num Topics = 3  has Coherence Value of 0.4752
Num Topics = 4  has Coherence Value of 0.5152
Num Topics = 5  has Coherence Value of 0.5159
Num Topics = 6  has Coherence Value of 0.5372
Num Topics = 7  has Coherence Value of 0.5491
Num Topics = 8  has Coherence Value of 0.521
Num Topics = 9  has Coherence Value of 0.5347
Num Topics = 10  has Coherence Value of 0.5068
Num Topics = 11  has Coherence Value of 0.5373
Num Topics = 12  has Coherence Value of 0.5352
Num Topics = 13  has Coherence Value of 0.5019
Num Topics = 14  has Coherence Value of 0.5122
Num Topics = 15  has Coherence Value of 0.5594
Num Topics = 16  has Coherence Value of 0.5308
Num Topics = 17  has Coherence Value of 0.524
Num Topics = 18  has Coherence Value of 0.5244
Num Topics = 19  has Coherence Value of 0.5192
Num Topics = 20  has Coherence Value of 0.4962
Num Topics = 21  has Coherence Value of 0.486
Num Topics = 22  has Coherence Value of 0.5201
Num Topics = 23  has Coh

In [47]:
type(model_list)
len(model_list)
print("Coherence score = ", coherence_values[31])
model_list[31]

Coherence score =  0.593089246369416


In [48]:
# Set training parameters.
num_topics = 33
chunksize = 10000 # size of the doc looked at every pass
passes = 40 # number of passes through documents
iterations = 100
eval_every = 1  # Don't evaluate model perplexity, takes too much time.

# Make an index to word dictionary.
temp = docs_dict[0]  # This is only to "load" the dictionary.
id2word = docs_dict.id2token

%time model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes, eval_every=eval_every)

Wall time: 5min


In [49]:
#Print all the topics
for i in range(0, model.num_topics):
    print ('Topic', i+1 , ' ', model.print_topic(i))
    print("-------------------------------------------------------------")

Topic 1   0.003*"deep state" + 0.001*"survival rate" + 0.001*"vaccine cause" + 0.001*"covid vaccine" + 0.001*"vaccine cause autism" + 0.001*"cause autism" + 0.001*"5g tower" + 0.001*"vaccine 5g" + 0.001*"bill gate" + 0.001*"virus vaccine"
-------------------------------------------------------------
Topic 2   0.003*"deep state" + 0.002*"vaccine cause" + 0.001*"virus recovery" + 0.001*"vaccine virus" + 0.001*"vaccine cause autism" + 0.001*"cause autism" + 0.001*"virus recovery rate" + 0.001*"recovery rate" + 0.001*"covid vaccine" + 0.001*"vaccine virus recovery"
-------------------------------------------------------------
Topic 3   0.004*"vaccine cause" + 0.004*"vaccine cause autism" + 0.004*"cause autism" + 0.003*"deep state" + 0.003*"vaccine family" + 0.002*"covid vaccine" + 0.001*"believe vaccine" + 0.001*"people believe" + 0.001*"believe vaccine cause" + 0.001*"bill gate"
-------------------------------------------------------------
Topic 4   0.004*"deep state" + 0.004*"vaccine cau

Topic 28   0.004*"deep state" + 0.001*"bill gate" + 0.001*"vaccine cause" + 0.001*"cause autism" + 0.001*"vaccine cause autism" + 0.001*"dangerous unethical" + 0.001*"helped harmed" + 0.001*"exemption dangerous unethical" + 0.001*"mandate removal" + 0.001*"vaccination helped"
-------------------------------------------------------------
Topic 29   0.004*"vaccine cause autism" + 0.004*"cause autism" + 0.004*"vaccine cause" + 0.002*"deep state" + 0.002*"kill people" + 0.002*"kill people year" + 0.002*"people year" + 0.002*"estimate flu kill" + 0.002*"flu globally" + 0.002*"estimate flu"
-------------------------------------------------------------
Topic 30   0.003*"covid vaccine" + 0.002*"vaccine cause" + 0.002*"deep state" + 0.002*"vaccine cause autism" + 0.002*"cause autism" + 0.001*"paul kangas" + 0.001*"kangas governor" + 0.001*"paul kangas governor" + 0.001*"vaccine unnecessary" + 0.001*"sweden proved paul"
-------------------------------------------------------------
Topic 31   0.0

# Other Hyperparameters:

In [326]:
# supporting function
def compute_coherence_values(corpus, dictionary, k, a, b):
    lda_model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=k, random_state=100, \
                         chunksize=100, passes=10, alpha=a, eta=b)
    
    coherence_model_lda = CoherenceModel(model=lda_model, texts=docs, dictionary=dictionary, coherence='c_v')
    
    return coherence_model_lda.get_coherence()

In [327]:
import tqdm

grid = {}
grid['Validation_Set'] = {}

# Topics range
min_topics = 2
max_topics = 9
step_size = 1
topics_range = range(min_topics, max_topics, step_size)

# Alpha parameter
alpha = list(np.arange(0.01, 1, 0.3))
alpha.append('symmetric')
alpha.append('asymmetric')

# Beta parameter
beta = list(np.arange(0.01, 1, 0.3))
beta.append('symmetric')

In [328]:
# Validation sets
num_of_docs = len(corpus)
corpus_sets = [gensim.utils.ClippedCorpus(corpus, int(num_of_docs*0.75)), corpus]
corpus_title = ['75% Corpus', '100% Corpus']
model_results = {'Validation_Set': [], 'Topics': [], 'Alpha': [], 'Beta': [], 'Coherence': []}

# Can take a long time to run
if 1 == 1:
    pbar = tqdm.tqdm(total=540)
    
    # iterate through validation corpuses
    for i in range(len(corpus_sets)):
        # iterate through number of topics
        for k in topics_range:
            # iterate through alpha values
            for a in alpha:
                # iterare through beta values
                for b in beta:
                    # get the coherence score for the given parameters
                    cv = compute_coherence_values(corpus=corpus_sets[i], dictionary=docs_dict, 
                                                  k=k, a=a, b=b)
                    # Save the model results
                    model_results['Validation_Set'].append(corpus_title[i])
                    model_results['Topics'].append(k)
                    model_results['Alpha'].append(a)
                    model_results['Beta'].append(b)
                    model_results['Coherence'].append(cv)
                    
                    pbar.update(1)
    pd.DataFrame(model_results)
    pbar.close()



  0%|          | 0/540 [04:22<?, ?it/s]


  0%|          | 1/540 [00:13<2:02:22, 13.62s/it]

  0%|          | 2/540 [00:28<2:09:42, 14.47s/it]

  1%|          | 3/540 [00:44<2:16:54, 15.30s/it]

  1%|          | 4/540 [01:01<2:20:10, 15.69s/it]

  1%|          | 5/540 [01:16<2:18:43, 15.56s/it]

  1%|          | 6/540 [01:30<2:12:22, 14.87s/it]

  1%|▏         | 7/540 [01:45<2:12:48, 14.95s/it]

  1%|▏         | 8/540 [02:01<2:15:57, 15.33s/it]

  2%|▏         | 9/540 [02:18<2:20:35, 15.89s/it]

  2%|▏         | 10/540 [02:34<2:20:13, 15.87s/it]

  2%|▏         | 11/540 [02:47<2:13:47, 15.18s/it]

  2%|▏         | 12/540 [03:02<2:13:01, 15.12s/it]

  2%|▏         | 13/540 [03:19<2:17:01, 15.60s/it]

  3%|▎         | 14/540 [03:37<2:23:20, 16.35s/it]

  3%|▎         | 15/540 [03:54<2:23:11, 16.37s/it]

  3%|▎         | 16/540 [04:07<2:15:53, 15.56s/it]

  3%|▎         | 17/540 [04:22<2:14:05, 15.38s/it]

  3%|▎         | 18/540 [04:38<2:15:24, 15.56s/it]

  4%|▎         | 19/540 [04:5

 51%|█████     | 276/540 [1:28:32<1:28:03, 20.01s/it]

 51%|█████▏    | 277/540 [1:28:51<1:26:47, 19.80s/it]

 51%|█████▏    | 278/540 [1:29:12<1:28:18, 20.22s/it]

 52%|█████▏    | 279/540 [1:29:35<1:31:01, 20.93s/it]

 52%|█████▏    | 280/540 [1:29:54<1:27:49, 20.27s/it]

 52%|█████▏    | 281/540 [1:30:11<1:23:30, 19.34s/it]

 52%|█████▏    | 282/540 [1:30:30<1:23:27, 19.41s/it]

 52%|█████▏    | 283/540 [1:30:51<1:25:04, 19.86s/it]

 53%|█████▎    | 284/540 [1:31:13<1:26:53, 20.36s/it]

 53%|█████▎    | 285/540 [1:31:32<1:24:42, 19.93s/it]

 53%|█████▎    | 286/540 [1:31:49<1:20:26, 19.00s/it]

 53%|█████▎    | 287/540 [1:32:08<1:20:30, 19.09s/it]

 53%|█████▎    | 288/540 [1:32:28<1:21:32, 19.42s/it]

 54%|█████▎    | 289/540 [1:32:50<1:23:46, 20.03s/it]

 54%|█████▎    | 290/540 [1:33:08<1:21:42, 19.61s/it]

 54%|█████▍    | 291/540 [1:33:25<1:17:47, 18.74s/it]

 54%|█████▍    | 292/540 [1:33:45<1:18:52, 19.08s/it]

 54%|█████▍    | 293/540 [1:34:06<1:20:50, 19.64s/it]

 54%|█████

In [329]:
pd.DataFrame(model_results).to_csv('lda_tuning_results.csv', index=False)

# Visualize 'optimal' LDA model

In [50]:
import pyLDAvis
pyLDAvis.gensim_models
import pyLDAvis.gensim_models
import warnings
pyLDAvis.enable_notebook()
warnings.filterwarnings("ignore", category=DeprecationWarning) 

In [53]:
#pcoa:Principal Coordinate Analysis (aka Classical Multidimensional Scaling)
pyLDAvis.gensim_models.prepare(model, corpus, docs_dict)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
20    -0.305559 -0.006114       1        1  5.380549
17     0.015089 -0.235277       2        1  4.608120
28     0.012908 -0.054907       3        1  3.707905
14     0.010820 -0.026506       4        1  3.565855
6      0.008825 -0.005219       5        1  3.560961
31     0.010674  0.001010       6        1  3.485452
3      0.009988 -0.020447       7        1  3.232954
2      0.014253 -0.031442       8        1  3.157058
23     0.008874 -0.003839       9        1  3.122160
24     0.008465  0.023916      10        1  3.070566
30     0.005200 -0.001733      11        1  2.992969
29     0.011544  0.019655      12        1  2.977675
10     0.008918  0.018903      13        1  2.935388
0      0.009721  0.014298      14        1  2.932561
7      0.009831  0.036084      15        1  2.930780
22     0.010070 -0.001397      16        1  2.922212
4      0.010176  0.016279      17        1  2.899758
27     0.010297  0.009491      18        1  2.897774
9      0.009212  0.033325      19        1  2.848473
1      0.010564  0.010117      20        1  2.841579
32     0.009994 -0.008140      21        1  2.833732
21     0.007477  0.023504      22        1  2.800400
8      0.010770  0.034010      23        1  2.800148
19     0.012161  0.005301      24        1  2.763511
16     0.008722  0.008166      25        1  2.690594
11     0.009552  0.012148      26        1  2.678175
12     0.006619  0.011730      27        1  2.673009
18     0.009126  0.011063      28        1  2.636626
25     0.007712  0.025670      29        1  2.622981
13     0.005298  0.020202      30        1  2.443106
5      0.005437  0.017158      31        1  2.395871
15     0.009131  0.014252      32        1  2.335684
26     0.008133  0.028739      33        1  2.255415, topic_info=                            Term        Freq       Total Category  logprob  \
454     fasttracked experimental  111.000000  111.000000  Default  30.0000   
451             dont belong free  110.000000  110.000000  Default  29.0000   
466              medical mandate  110.000000  110.000000  Default  28.0000   
444          belong free society  110.000000  110.000000  Default  27.0000   
443                  belong free  110.000000  110.000000  Default  26.0000   
...                          ...         ...         ...      ...      ...   
2215                think doesnt    3.512524    5.179762  Topic33  -7.2876   
70693                 vaccine tv    3.512524    7.079748  Topic33  -7.2876   
73815             believe taking    3.512524    4.620043  Topic33  -7.2876   
94166              funny believe    3.512524    4.602249  Topic33  -7.2876   
113828              person think    3.512524    4.625185  Topic33  -7.2876   

        loglift  
454     30.0000  
451     29.0000  
466     28.0000  
444     27.0000  
443     26.0000  
...         ...  
2215     3.4034  
70693    3.0909  
73815    3.5178  
94166    3.5216  
113828   3.5167  

[1785 rows x 6 columns], token_table=        Topic      Freq                    Term
term                                           
118424      3  0.970929            1st approved
118425      3  0.970929  1st approved influenza
3001        1  0.070069              5g antenna
3001        3  0.070069              5g antenna
3001        4  0.035034              5g antenna
...       ...       ...                     ...
64683       8  0.577812     yep expected rushed
165752      7  0.574091               youve met
24882      32  0.955819               yr liable
24883      32  0.955819        yr liable return
112833     25  0.910282             yup vaccine

[5247 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[21, 18, 29, 15, 7, 32, 4, 3, 24, 25, 31, 30, 11, 1, 8, 23, 5, 28, 10, 2, 33, 22, 9, 20, 17, 12, 13, 19, 26, 14, 6, 16, 27])

In [54]:
# mmds:Metric Multidimensional Scaling
pyLDAvis.gensim_models.prepare(model, corpus, docs_dict, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
20     0.218209 -0.251324       1        1  5.379738
17     0.230990 -0.126031       2        1  4.606509
28     0.262447 -0.007653       3        1  3.708764
14     0.242257  0.093278       4        1  3.567017
6      0.048682 -0.254701       5        1  3.560995
31    -0.210813 -0.167056       6        1  3.485277
3     -0.133591 -0.181042       7        1  3.232988
2     -0.162360 -0.021913       8        1  3.157096
23    -0.244447  0.073282       9        1  3.122199
24    -0.072800 -0.110329      10        1  3.071600
30    -0.078208 -0.223547      11        1  2.993003
29     0.012286  0.237544      12        1  2.976572
10    -0.128012  0.147586      13        1  2.935421
0     -0.191395  0.137150      14        1  2.932595
7     -0.189022 -0.098333      15        1  2.931028
22    -0.014464 -0.203705      16        1  2.922245
4      0.101724 -0.166536      17        1  2.900650
27     0.057996 -0.122908      18        1  2.897810
9      0.083867  0.231312      19        1  2.848507
1     -0.185423  0.047231      20        1  2.841609
32     0.008162  0.141447      21        1  2.833765
21    -0.117217  0.207679      22        1  2.800433
8     -0.052142  0.223448      23        1  2.800103
19     0.123702 -0.063386      24        1  2.764261
16     0.168300 -0.015594      25        1  2.690626
11     0.150367  0.070680      26        1  2.678206
12     0.111661  0.170619      27        1  2.673043
18     0.076356  0.071364      28        1  2.637217
25     0.168429  0.141551      29        1  2.622021
13    -0.069531  0.076063      30        1  2.443139
5     -0.208713 -0.032393      31        1  2.395109
15     0.005658 -0.046034      32        1  2.335004
26    -0.012954  0.022251      33        1  2.255449, topic_info=                            Term        Freq       Total Category  logprob  \
454     fasttracked experimental  111.000000  111.000000  Default  30.0000   
451             dont belong free  110.000000  110.000000  Default  29.0000   
466              medical mandate  110.000000  110.000000  Default  28.0000   
444          belong free society  110.000000  110.000000  Default  27.0000   
443                  belong free  110.000000  110.000000  Default  26.0000   
...                          ...         ...         ...      ...      ...   
2215                think doesnt    3.512577    5.180016  Topic33  -7.2876   
70693                 vaccine tv    3.512577    7.079753  Topic33  -7.2876   
73815             believe taking    3.512577    4.620103  Topic33  -7.2876   
94166              funny believe    3.512577    4.602424  Topic33  -7.2876   
113828              person think    3.512577    4.625411  Topic33  -7.2876   

        loglift  
454     30.0000  
451     29.0000  
466     28.0000  
444     27.0000  
443     26.0000  
...         ...  
2215     3.4034  
70693    3.0909  
73815    3.5178  
94166    3.5216  
113828   3.5166  

[1785 rows x 6 columns], token_table=        Topic      Freq                    Term
term                                           
118424      3  0.970711            1st approved
118425      3  0.970711  1st approved influenza
3001        1  0.070066              5g antenna
3001        3  0.070066              5g antenna
3001        4  0.035033              5g antenna
...       ...       ...                     ...
64683       8  0.577807     yep expected rushed
165752      7  0.574086               youve met
24882      32  0.956021               yr liable
24883      32  0.956021        yr liable return
112833     25  0.910273             yup vaccine

[5247 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[21, 18, 29, 15, 7, 32, 4, 3, 24, 25, 31, 30, 11, 1, 8, 23, 5, 28, 10, 2, 33, 22, 9, 20, 17, 12, 13, 19, 26, 14, 6, 16, 27])

In [58]:
#tsne:t-distributed Stochastic Neighbor Embedding
pyLDAvis.gensim_models.prepare(model, corpus, docs_dict, mds='tsne')

PreparedData(topic_coordinates=                x           y  topics  cluster      Freq
topic                                                   
20    -156.280563  -44.476768       1        1  5.379697
17     -71.461990  121.194145       2        1  4.606288
28    -130.868271   22.523844       3        1  3.710094
14    -103.081474   70.105736       4        1  3.565852
6      120.036835   17.077663       5        1  3.560816
31      81.974403   85.556091       6        1  3.485247
3       79.368782  -68.985352       7        1  3.232951
2       73.754097   36.089596       8        1  3.157058
23    -101.789680  -73.355850       9        1  3.122163
24      15.591368  113.500648      10        1  3.071569
30      46.366360 -110.153259      11        1  2.992963
29      34.067696   73.545723      12        1  2.977676
10     -56.384693  -97.667908      13        1  2.935671
0      -27.063328   94.553520      14        1  2.932561
7      -65.423386  -51.833164      15        1  2.930994
22      32.142372   34.812511      16        1  2.922211
4       44.240055  -38.782940      17        1  2.899756
27      21.606024  -73.238197      18        1  2.897773
9       87.032623  -21.824699      19        1  2.848472
1      -21.303646  -70.706871      20        1  2.841726
32     -60.186264   -8.034520      21        1  2.833732
21     -98.564827  -19.141584      22        1  2.800400
8       -9.023562 -112.193573      23        1  2.800090
19     -55.336632   63.045406      24        1  2.764228
16     -22.298874   -3.360628      25        1  2.691446
11      -7.886399   59.982914      26        1  2.677892
12     -79.459526   25.642059      27        1  2.672502
18       4.365372  -37.749489      28        1  2.636625
25      50.302204   -0.053919      29        1  2.622980
13     -39.513187   28.333384      30        1  2.443105
5       -3.229049   25.650442      31        1  2.395079
15      14.321824   -4.520929      32        1  2.334966
26     -32.141949  -34.964069      33        1  2.255415, topic_info=                            Term        Freq       Total Category  logprob  \
454     fasttracked experimental  111.000000  111.000000  Default  30.0000   
451             dont belong free  110.000000  110.000000  Default  29.0000   
466              medical mandate  110.000000  110.000000  Default  28.0000   
444          belong free society  110.000000  110.000000  Default  27.0000   
443                  belong free  110.000000  110.000000  Default  26.0000   
...                          ...         ...         ...      ...      ...   
2215                think doesnt    3.512523    5.179893  Topic33  -7.2876   
70693                 vaccine tv    3.512523    7.080039  Topic33  -7.2876   
73815             believe taking    3.512523    4.620043  Topic33  -7.2876   
94166              funny believe    3.512523    4.602249  Topic33  -7.2876   
113828              person think    3.512523    4.625185  Topic33  -7.2876   

        loglift  
454     30.0000  
451     29.0000  
466     28.0000  
444     27.0000  
443     26.0000  
...         ...  
2215     3.4034  
70693    3.0909  
73815    3.5178  
94166    3.5216  
113828   3.5167  

[1785 rows x 6 columns], token_table=        Topic      Freq                    Term
term                                           
118424      3  0.970374            1st approved
118425      3  0.970374  1st approved influenza
3001        1  0.070068              5g antenna
3001        3  0.070068              5g antenna
3001        4  0.035034              5g antenna
...       ...       ...                     ...
64683       8  0.577811     yep expected rushed
165752      7  0.574090               youve met
24882      32  0.956032               yr liable
24883      32  0.956032        yr liable return
112833     25  0.910067             yup vaccine

[5247 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[21, 18, 29, 15, 7, 32, 4, 3, 24, 25, 31, 3